#### CSCE 670 :: Information Storage and Retrieval :: Texas A&M University :: Spring 2019


# Homework 3:   Collaborative Filtering + Matrix Factorization

### 100 points [6% of your final grade]

### Due: Wednesday, March 27, 2019 by 11:59pm

*Goals of this homework:* Understand how collaborative filtering and matrix factorization works. Explore different methods for real-world recommendation senarios.

*Submission instructions (eCampus):* To submit your homework, rename this notebook as `UIN_hw3.ipynb`. For example, my homework submission would be something like `555001234_hw3.ipynb`. Submit this notebook via eCampus (look for the homework 3 assignment there). Your notebook should be completely self-contained, with the results visible in the notebook. We should not have to run any code from the command line, nor should we have to run your code within the notebook (though we reserve the right to do so). So please run all the cells for us, and then submit.

*Late submission policy:* For this homework, you may use as many late days as you like (up to the 5 total allotted to you).

*Collaboration policy:* You are expected to complete each homework independently. Your solution should be written by you without the direct aid or help of anyone else. However, we believe that collaboration and team work are important for facilitating learning, so we encourage you to discuss problems and general problem approaches (but not actual solutions) with your classmates. You may post on Piazza, search StackOverflow, etc. But if you do get help in this way, you must inform us by **filling out the Collaboration Declarations at the bottom of this notebook**. 

*Example: I found helpful code on stackoverflow at https://stackoverflow.com/questions/11764539/writing-fizzbuzz that helped me solve Problem 2.*

The basic rule is that no student should explicitly share a solution with another student (and thereby circumvent the basic learning process), but it is okay to share general approaches, directions, and so on. If you feel like you have an issue that needs clarification, feel free to contact either me or the TA.

# Part 1. Collaborative Filtering (50 points)

In this part, you will implement collaborative filtering on the [MovieLens Latest Datasets](http://files.grouplens.org/datasets/movielens/ml-latest-small-README.html). After removing users who left less than 20 ratings and movies with less than 20 ratings, the provided dataset has only ~1,200 items and ~500 users. You can also check the title and genres of each movie in *movies_info.csv*.

As background, read [Collaborative Filtering Recommender Systems](http://files.grouplens.org/papers/FnT%20CF%20Recsys%20Survey.pdf) and refer to the course slides `week06rec.pdf` for collaborative filtering.

## 1.1 Load the Data

Please download the dataset from Piazza. There are about 65,000 ratings in total. We split the rating data into two set. You will train with 70% of the data (in *train_movie.csv*) and test on the remaining 30% of data (in *test_movie.csv*). Each of train and test files has lines having this format: UserID, MovieID, Rating. 

First you will need to load the data and store it with any structure you like. Please report the numbers of unique users and movies in the dataset. 

In [149]:
import csv
import numpy as np
import math

In [274]:
# load the data, then print out the number of
# movies and users in each of train and test sets.
# Your Code Here...
# use a user dictionary, key => user  value => list of movie to rating
def load_data(fileName):
    user_dict = {}
    movie_dict = {}
    with open(fileName) as csv_file:
        csv_reader = csv.reader(csv_file, delimiter = ',')
        for counter, row in enumerate(csv_reader):
            if counter > 0: 
                user_temp = {int(row[1]): int(row[2])}
                movie_temp = {int(row[0]): int(row[2])}
                if int(row[0]) not in user_dict:
                    user_dict[int(row[0])] = {}
                if int(row[1]) not in movie_dict:
                    movie_dict[int(row[1])] = {}
                user_dict.get(int(row[0]))[int(row[1])] = int(row[2])
                movie_dict.get(int(row[1]))[int(row[0])] = int(row[2])
    return user_dict, movie_dict, counter
            

In [275]:
def build_matrix(user_dict, movie_dict):
    res = np.zeros((len(user_dict), len(movie_dict)))
    for user, movies in user_dict.items():
        for movie in movies:
            res[user][movie] = user_dict.get(user).get(movie)
    return res



In [276]:
USER_NUM = len(train_user_dict)
MOVIE_NUM = len(train_movie_dict)

In [277]:
train_user_dict, train_movie_dict, train_counter = load_data("train_movie.csv")
test_user_dict, test_movie_dict, test_counter = load_data("test_movie.csv")

In [278]:
train_matrix = build_matrix(train_user_dict, train_movie_dict)
test_matrix = build_matrix(test_user_dict, test_movie_dict)


In [279]:
print(len(train_user_dict), len(train_movie_dict))
print(len(test_user_dict), len(test_movie_dict))

541 1211
541 1211


In [272]:
for movies in train_user_dict.values():
    for movie in movies:
        print(movie, movies.get(movie))

4 4
23 5
25 5
31 3
33 5
37 4
44 5
49 5
66 3
71 5
72 4
80 5
97 3
102 5
109 4
113 4
115 5
117 4
135 4
139 5
145 4
156 5
161 4
164 4
165 5
174 4
178 5
180 5
186 3
188 5
195 4
233 5
236 5
249 5
255 4
260 5
263 5
268 4
270 5
273 5
288 5
289 5
290 5
296 5
298 4
299 5
301 5
302 4
305 5
315 5
331 4
341 5
342 5
346 5
348 5
379 3
391 4
393 5
400 5
401 3
403 5
410 5
414 3
420 3
437 4
455 5
460 4
465 4
469 5
475 5
484 5
487 5
494 4
496 4
499 5
507 5
509 4
511 4
518 4
533 5
546 5
550 4
559 5
563 5
565 4
570 3
571 5
575 5
583 4
584 2
585 4
586 4
593 5
601 5
617 4
619 5
627 5
628 5
630 5
633 5
637 5
640 5
641 4
645 5
646 5
649 5
666 4
669 1
672 3
674 5
681 5
700 5
701 5
706 4
710 4
717 5
719 4
723 5
727 5
728 5
731 4
740 4
831 5
99 3
102 4
717 4
907 4
949 3
1019 4
1026 4
1064 4
1090 4
1106 4
1117 4
1144 3
1147 2
1163 3
1180 3
1190 3
16 0
156 0
185 0
193 0
215 5
230 0
330 0
339 3
475 0
488 0
496 2
521 4
558 0
671 0
728 5
11 3
17 2
22 3
23 2
26 3
27 3
64 5
72 2
80 5
82 5
105 5
107 4
108 4
114 3
118 4
1

255 2
256 3
267 3
270 2
274 3
275 3
278 2
279 3
288 4
289 2
291 2
292 4
293 4
303 3
306 4
307 4
312 3
313 3
323 3
336 2
339 2
340 3
360 3
362 4
365 4
368 2
386 3
393 2
394 4
401 3
402 3
403 2
408 4
410 3
411 2
413 2
415 2
424 3
428 2
429 4
431 3
449 4
454 4
463 2
465 2
478 5
479 3
484 2
512 3
513 2
514 2
518 3
533 2
559 3
569 2
574 3
575 4
577 3
591 2
597 1
608 3
609 2
623 3
625 3
631 3
633 3
635 3
641 2
644 2
645 3
649 3
659 2
660 2
663 2
667 2
668 1
673 3
677 2
682 3
684 4
686 2
692 2
694 3
707 3
716 3
717 4
724 3
727 3
749 3
750 3
752 2
753 4
760 3
761 2
763 3
773 3
780 4
781 3
794 2
795 1
801 3
813 2
817 3
818 4
829 4
844 3
848 3
850 3
855 3
858 2
861 2
870 3
871 3
873 2
883 1
886 2
888 3
891 2
894 2
895 4
896 2
900 2
904 2
906 3
908 3
913 3
918 3
920 3
925 2
932 4
943 3
944 3
945 4
946 3
952 2
955 2
956 4
959 3
961 2
967 4
970 3
975 3
976 3
977 2
978 4
981 4
983 3
985 3
986 4
997 2
999 2
1000 2
1001 2
1002 3
1004 3
1005 4
1006 2
1008 3
1017 2
1018 2
1022 3
1024 4
1026 2
1027 3
103

797 3
821 4
827 5
828 4
839 3
844 4
847 4
850 4
852 3
855 4
869 4
886 3
888 5
889 4
894 3
897 3
907 5
918 4
920 5
922 4
926 3
927 5
932 4
933 1
935 4
940 4
943 4
944 4
956 4
960 3
962 5
963 4
968 4
974 4
978 4
980 3
981 5
983 3
989 4
995 4
998 4
1000 4
1001 4
1004 5
1011 3
1012 3
1015 4
1020 4
1021 4
1023 4
1024 4
1025 4
1026 4
1028 5
1029 4
1031 4
1035 4
1040 4
1046 4
1050 4
1052 4
1056 5
1060 3
1064 5
1066 3
1070 3
1071 4
1072 3
1074 4
1075 3
1076 4
1081 4
1086 4
1090 4
1091 2
1092 3
1094 5
1095 4
1097 4
1101 3
1104 4
1106 4
1107 5
1110 3
1113 5
1115 4
1120 4
1121 5
1125 4
1128 4
1130 4
1132 4
1135 4
1138 4
1141 4
1144 5
1145 5
1147 4
1151 3
1157 4
1160 4
1163 5
1164 3
1168 3
1171 3
1173 5
1175 4
1177 4
1179 5
1180 5
1181 4
1182 4
1183 4
1185 4
1187 4
1188 5
1195 4
1197 4
1198 3
1199 4
1205 4
1208 4
1209 4
1210 5
23 4
37 2
38 3
43 3
50 4
71 3
80 5
92 5
99 5
106 5
113 3
114 4
116 4
117 4
145 2
149 3
156 4
166 2
169 2
171 4
172 4
174 4
177 3
199 5
202 4
217 4
229 4
237 3
240 4
242 3
26

212 3
217 3
253 4
256 2
267 3
270 2
277 3
288 4
292 3
293 3
299 4
302 3
306 3
363 1
375 2
389 3
394 4
395 3
396 3
397 2
401 4
407 3
415 2
423 3
426 2
436 3
439 2
450 4
465 4
470 2
472 4
473 4
480 3
499 4
519 4
534 2
541 3
542 1
553 3
567 3
575 4
584 3
585 3
596 4
610 3
629 3
637 3
649 2
717 4
720 2
722 3
730 4
735 4
737 4
738 3
756 3
765 4
767 4
769 2
771 3
775 3
785 2
788 3
792 4
795 3
797 4
800 4
809 4
810 3
814 4
837 3
842 2
844 1
852 4
854 3
856 3
864 4
876 3
879 3
880 3
890 3
893 3
895 4
897 4
898 3
899 4
905 3
920 4
37 4
48 3
99 5
116 3
232 5
236 3
253 2
268 1
281 4
291 2
295 3
296 4
307 5
308 0
309 5
318 5
321 3
326 5
342 4
346 1
374 0
416 3
420 3
422 5
528 3
619 3
702 3
717 5
735 4
753 4
769 3
781 4
790 3
799 3
811 0
823 3
824 5
825 4
828 3
829 4
844 2
869 3
871 3
878 5
892 3
918 3
922 3
924 5
927 0
932 3
942 2
952 3
967 3
997 4
1004 4
1025 3
1058 3
1068 2
1094 4
1098 3
1100 2
1104 4
1108 2
1109 3
1121 4
3 3
5 3
6 3
9 5
14 5
16 3
18 4
19 5
22 4
25 4
29 4
35 3
48 3
67 4
68 3
73 

575 0
578 4
602 2
619 4
626 3
633 5
637 3
649 5
667 4
668 3
670 4
671 2
672 3
674 5
675 3
681 0
682 5
706 3
712 3
719 3
737 2
741 3
747 4
748 4
751 1
752 3
756 3
765 3
766 2
767 3
771 3
774 2
778 0
781 3
784 3
786 3
787 2
788 3
789 3
790 3
797 3
802 3
808 3
810 2
814 3
818 4
819 3
821 4
823 4
828 4
836 3
841 4
848 0
850 2
851 3
854 3
860 3
861 0
865 4
876 2
884 3
888 1
890 4
893 3
896 3
901 3
905 3
909 4
913 0
923 4
926 3
930 4
933 2
937 3
939 4
941 2
944 4
950 4
954 3
958 1
960 3
962 4
963 3
968 1
971 0
973 3
974 3
979 3
980 3
981 2
984 4
988 3
991 2
999 4
1003 3
1014 4
1015 3
1023 3
1025 3
1026 4
1030 4
1032 3
1035 4
1037 3
1039 3
1040 3
1042 3
1046 4
1049 3
1050 4
1057 2
1060 3
1064 4
1065 5
1066 2
1069 2
1071 3
1075 5
1077 3
1078 2
1082 1
1089 3
1090 4
1095 4
1098 4
1100 3
1104 2
1109 3
1113 4
1115 3
1117 3
1119 3
1120 4
1122 1
1125 3
1134 4
1135 4
1145 4
1147 3
1163 4
1166 5
1168 4
1186 4
1188 4
1189 3
1194 5
1195 4
1198 3
1199 5
1204 2
1206 5
1207 2
4 4
9 0
10 4
11 2
17 5
19 0
20

...

344 4
346 5
352 3
353 2
363 4
364 4
371 3
375 2
388 4
394 3
395 2
396 2
399 3
400 2
401 2
405 3
407 3
415 3
416 5
418 4
420 3
422 3
423 2
424 4
425 2
426 2
428 3
431 5
432 3
436 3
443 3
450 4
458 3
464 2
465 3
466 4
468 3
470 2
472 4
473 4
476 4
480 4
483 2
492 3
495 3
496 3
499 4
500 1
505 2
507 3
509 4
512 4
514 4
519 3
523 4
524 3
528 5
529 3
534 3
541 3
545 4
547 3
551 2
555 4
557 2
563 3
567 4
571 3
572 3
574 5
576 2
586 3
591 3
596 4
597 3
598 3
602 3
606 2
609 3
612 4
614 4
616 3
624 2
625 4
629 3
632 2
633 4
634 3
635 2
636 2
637 4
642 5
645 4
649 4
661 4
662 3
663 3
664 4
665 3
678 2
680 2
682 4
685 4
686 5
692 3
695 2
703 2
705 3
706 4
709 4
710 2
720 0
730 3
732 4
734 3
735 3
738 3
746 4
751 3
763 4
766 4
767 4
771 3
775 4
781 4
785 4
789 3
790 4
791 4
795 2
799 4
802 3
805 2
807 1
809 3
810 2
814 5
815 3
819 4
821 4
823 4
824 5
825 2
827 4
828 4
848 4
850 4
859 5
864 1
865 1
866 3
868 5
869 3
875 4
878 4
887 4
888 2
889 3
891 3
896 4
897 3
900 4
902 3
904 4
906 4
907 5
908 

228 4
230 4
232 3
234 4
239 1
240 4
242 1
243 2
247 3
248 5
249 4
250 3
251 4
252 5
262 1
266 1
273 5
279 2
284 4
287 1
295 2
296 0
297 3
299 2
304 1
308 2
311 1
313 2
318 2
319 2
329 4
330 1
331 3
334 0
344 0
350 0
351 2
373 1
398 0
401 3
406 1
410 0
413 4
421 2
422 1
424 2
426 3
434 3
449 1
451 1
452 1
455 0
460 1
464 1
465 1
472 4
473 4
475 4
480 3
482 0
483 1
495 2
534 0
542 4
547 1
558 1
561 2
575 2
590 3
602 1
612 3
619 1
637 0
646 3
648 2
659 2
663 4
669 2
678 4
680 2
696 1
700 3
712 1
717 1
729 2
751 2
759 3
761 0
764 3
767 1
769 4
772 3
778 1
790 4
791 1
819 2
821 4
823 0
828 3
830 5
831 4
836 2
842 2
848 3
853 3
866 4
867 0
873 1
876 2
889 1
890 4
910 5
920 3
925 1
933 2
934 2
940 3
946 2
967 0
971 1
994 2
997 0
998 3
1016 2
1017 1
1020 2
1033 1
1040 2
1046 3
1049 2
1060 2
1069 0
1071 2
1081 0
1085 3
1098 3
1112 2
1124 1
1135 3
1139 0
1140 2
1147 0
1156 1
1161 1
1170 3
1174 1
1191 4
16 1
141 3
204 3
365 0
366 4
373 2
522 5
533 4
657 3
696 3
735 2
748 4
885 4
886 4
888 4
890 5

504 3
507 3
519 2
521 4
523 4
524 2
526 3
529 3
534 3
539 3
546 4
548 4
551 3
554 3
557 4
571 4
575 4
585 2
586 4
587 4
595 3
601 5
602 3
608 4
609 2
612 4
614 4
619 3
625 3
626 4
633 4
635 4
641 3
645 4
648 3
652 3
654 4
662 3
674 3
680 3
682 4
686 4
700 3
703 4
706 3
707 3
710 5
720 2
726 3
731 5
735 4
738 3
745 4
746 3
751 2
760 4
763 4
767 2
772 4
775 4
776 3
777 4
798 2
804 4
806 4
814 3
816 2
818 5
819 4
823 3
829 3
844 3
846 2
848 4
850 3
853 3
861 2
863 3
870 3
873 3
875 3
881 3
888 2
892 4
907 4
911 4
918 4
920 5
925 3
927 4
929 3
932 4
933 3
934 3
943 3
945 2
947 3
948 3
949 3
952 4
956 3
958 3
960 3
975 3
977 3
981 4
982 2
985 2
995 4
1000 3
1001 3
1004 3
1006 2
1009 3
1011 2
1017 3
1021 3
1025 1
1026 4
1031 3
1032 3
1033 4
1035 3
1037 2
1041 3
1052 2
1062 3
1064 5
1066 3
1067 2
1068 2
1071 5
1076 4
1090 3
1093 4
1094 4
1100 4
1105 4
1106 3
1111 4
1113 3
1114 2
1116 4
1117 3
1128 4
1136 4
1137 3
1139 4
1142 4
1143 3
1144 4
1145 4
1151 2
1153 2
1155 3
1159 4
1161 3
1163 3
116

875 3
880 1
887 4
888 3
890 4
894 3
895 2
896 3
897 3
905 3
906 3
908 4
923 1
927 3
932 2
934 1
936 3
943 3
946 3
952 4
958 4
966 2
972 5
978 3
981 4
983 3
986 4
991 4
995 4
996 4
998 3
1004 3
1016 2
1028 4
1029 3
1038 2
1046 3
1063 5
1070 3
1085 3
1090 3
1092 2
1094 3
1098 3
1100 3
1104 3
1105 3
1106 3
1108 4
1109 3
1110 3
1111 3
1112 3
1113 4
1115 3
1116 3
1118 3
1120 4
1121 3
1135 3
1144 3
1149 3
1153 4
1155 3
1159 4
1162 3
1164 4
1166 4
1167 3
1171 3
1174 3
1177 4
1178 3
1181 5
1182 3
1183 4
1187 3
1188 4
1189 4
1194 3
1195 5
1196 4
1197 3
1198 3
1199 4
1200 4
1201 3
1202 3
1204 4
1207 4
1209 5
0 4
5 1
6 3
7 3
11 5
22 5
23 4
25 5
26 4
31 2
33 5
42 2
45 3
54 1
72 4
73 2
80 5
89 3
90 4
104 3
108 5
109 3
114 5
118 4
122 4
123 4
134 4
135 5
136 1
142 2
143 5
145 5
146 1
160 4
161 3
167 4
170 4
171 4
172 5
174 4
179 4
181 4
191 3
195 1
199 4
203 1
207 1
217 5
224 5
226 4
233 4
239 5
240 5
250 4
253 4
256 2
258 5
260 5
262 5
264 5
267 4
268 5
269 4
273 5
274 5
278 5
279 4
280 5
281 5
283

56 3
58 3
63 3
65 2
77 3
78 3
80 3
86 3
87 2
91 4
97 3
99 4
100 3
101 3
102 4
112 2
113 3
114 3
117 2
119 2
123 2
126 4
127 2
129 2
131 1
136 2
138 1
140 1
145 3
149 2
153 1
154 2
156 4
158 1
159 2
162 0
163 3
164 1
166 3
169 1
170 2
171 3
172 3
173 3
174 3
176 2
177 2
180 3
181 3
187 3
189 4
190 3
191 2
194 3
195 4
196 3
197 3
198 1
201 2
202 3
203 3
206 2
207 3
208 2
209 4
213 3
215 3
233 2
240 0
243 2
244 1
253 3
254 2
255 3
257 3
258 4
259 3
260 3
263 2
267 4
269 0
270 2
273 2
274 3
278 3
279 3
287 3
288 4
296 3
298 3
301 4
302 4
303 3
304 3
305 4
315 3
320 3
326 4
331 3
335 2
336 2
338 4
339 2
342 2
345 2
346 4
353 4
359 3
371 2
375 2
379 4
381 3
383 2
386 4
389 3
390 3
391 4
392 0
394 4
396 3
397 2
398 4
400 2
404 4
406 3
407 3
408 3
410 3
411 4
413 2
414 3
415 4
416 5
420 3
422 4
423 4
424 4
428 4
429 4
431 5
432 2
434 3
435 3
436 3
438 3
443 3
444 3
445 3
448 3
449 4
450 3
454 4
455 4
457 4
461 4
464 4
465 3
466 3
467 3
470 2
473 2
478 3
479 4
480 4
482 1
493 3
496 3
499 3
502 

## 1.2 Implement User-based Collaborative Filtering

In this part, you will implement the basic User–User Collaborative Filtering algorithm introduced in the class. Given the ratings by each user, you are going to try different methods in calculating the similarities between users. You will use equation `(c)` in `week06rec.pdf` (Page 40) to aggregate ratings. Set k = 0.05. Just consider all users as neighbors. That is, while predicting how user $u$ will rate item $i$, $\widehat{C}$ includes all users who have ratings on i in the training set.

*For this memory-based algorithm, you can only rely on the ratings in training set to predict for the testing set. That is, you assume that you don't know any ratings information in the test set except that when you evalaute your model.*

### Cosine Similarity

First, you will try to calculate the similarity between users with cosine similary following the equation on page 16 of [Collaborative Filtering Recommender Systems](http://files.grouplens.org/papers/FnT%20CF%20Recsys%20Survey.pdf). And then you need to predict the rating for each (user, movie) tuple in the test set. *Note: you don't need to subtract user mean baseline from the ratings prior to computing the similarity.*

In [280]:
# Your Code Here...
# Predict for test set

def cos_similar(matrix, id_one, id_two):
    a = np.dot(matrix[id_one], matrix[id_two])
    b = sum(np.power(matrix[id_one], 2))
    c = sum(np.power(matrix[id_two], 2))
    return a / (math.sqrt(b) * math.sqrt(c))

def predict(user, movie, matrix, train_user_dict, mean_dict):
    aggregate = 0
    for i in range(USER_NUM):
        if (i is not user) and contains(i, movie, train_user_dict):
            aggregate += (cos_similar(matrix, i, user) * (matrix[i][movie] - mean_dict.get(i)))
    return aggregate * 0.05 
                          
def average(user, user_dict):   
    total = 0
    movies = user_dict.get(user)
    for movie in movies:
        total += movies.get(movie)
    return total / len(movies)
    

def mean_map(user_dict):
    res = {}
    total = 0
    for user, movies in user_dict.items():
        total = 0
        for movie in movies:
            total += movies.get(movie)
        res[user] = total / len(movies)
    return res;


def contains(user, movie, user_dict):
    if movie in user_dict.get(user):
        return True;
    return False


In [281]:
mean_dict = mean_map(train_user_dict)


In [282]:
result = {}
for user, movies in test_user_dict.items():
    for movie in movies:
        temp = mean_dict.get(user) + predict(user, movie, train_matrix, train_user_dict, mean_dict)
        result[(user, movie)] = temp

### Evaluation

You should evaluate your predictions using Mean Absolute Error and Root Mean Squared Error. 

In [317]:
def evaluation(result, test_user_dict, test_counter):
    MAE = 0
    RMSE = 0
    for user, movies in test_user_dict.items():
        for movie in movies:
            MAE += abs(movies.get(movie) - result.get((user, movie)))
            RMSE += pow((movies.get(movie) - result.get((user, movie))), 2)
    MAE /= test_counter
    RMSE = math.sqrt(RMSE / test_counter)

In [285]:
# Your Code Here...
# Report Mean Absolute Error and Root Mean Squared Error for test set
cos_MAE, cos_RMSE = evaluation(result, test_user_dict, test_counter)    
print(cos_MAE, cos_RMSE)  # 0.6903937198616398 0.8991489107420851


0.6903937198616398 0.8991489107420851


### Pearson correlation

Then, you will try to calculate the similarity between users with pearson correlation following `week06rec.pdf` (Page 37). And then you need to predict the rating for each (user, movie) tuple in the test set.

In [315]:
# Your Code Here...
# Predict for test set


def pearson_correlation(user_dict, id_one, id_two, mean_dict):
    a = 0
    b = 0
    c = 0
    for movie in user_dict.get(id_one):
        if movie in user_dict.get(id_two):
            a += (user_dict.get(id_one).get(movie) - mean_dict.get(id_one)) * (user_dict.get(id_two).get(movie) - mean_dict.get(id_two))
            b += pow(user_dict.get(id_one).get(movie) - mean_dict.get(id_one), 2)
            c += pow(user_dict.get(id_two).get(movie) - mean_dict.get(id_two), 2)
    if b * c == 0:
        return 0
    return a / math.sqrt(b * c)


def pearson_predict(user, movie, train_user_dict, mean_dict):
    aggregate = 0
    for i in range(len(train_user_dict)):
        if (i is not user) and contains(i, movie, train_user_dict):
            aggregate += (pearson_correlation(train_user_dict, user, i, mean_dict) * (train_user_dict.get(i).get(movie) - mean_dict.get(i)))
            print(user, i, pearson_correlation(train_user_dict, user, i, mean_dict))
    return aggregate * 0.05 
    


In [316]:
pearson_result = {}
for user, movies in test_user_dict.items():
    for movie in movies:
        temp = mean_dict.get(user) + pearson_predict(user, movie, train_user_dict, mean_dict)
        pearson_result[(user, movie)] = temp

0 18 0.2741911204736144
0 25 0.22052881541201594
0 26 0.09528133778115049
0 43 0.11960415567888476
0 53 0.27517502746215433
0 63 0.06928481994432427
0 84 -0.007196740687944209
0 87 0.13258827676028143
0 108 -0.28847592568777625
0 124 0.10701235768673893
0 145 0.3410482311544806
0 165 0.10980367130466533
0 169 -0.041066007665717115
0 179 0.45589494817454135
0 183 0.10384632039106124
0 196 -0.12699521019130378
0 199 -0.0009677918131388593
0 200 -0.11441814909230646
0 209 -0.07783002131586908
0 213 -0.04415996475474489
0 216 0.035470420808664395
0 240 0.25246605480331213
0 249 0.08068325233434477
0 261 0.18241049852002025
0 268 0.14747579610324474
0 276 0.154684706636662
0 281 0.7319489475106565
0 282 -0.045659541514770384
0 317 0.11111851672056922
0 340 -0.06778671721507555
0 369 0.3114388436629994
0 380 -0.041328516063821215
0 383 0.06146804487660849
0 414 -0.10333872486780145
0 420 0.44041760541007696
0 432 0.19547051758087505
0 438 0.18708258206528436
0 442 0.11950839542632649
0 477 0

0 529 0.15395589755214095
0 535 0.1971127359172762
0 16 0.252503163345075
0 26 0.09528133778115049
0 40 0.0801193126813568
0 43 0.11960415567888476
0 61 0.3009796665308055
0 63 0.06928481994432427
0 68 -0.1984439499207774
0 84 -0.007196740687944209
0 92 0.03547883279491774
0 93 -0.151776706563506
0 96 0.30072757565337416
0 97 0.6672979295912805
0 124 0.10701235768673893
0 142 -0.13441364782669685
0 153 0.37321457776350164
0 165 0.10980367130466533
0 170 0.15568124810739867
0 181 0.27766008394647
0 197 1.0
0 198 0.2556411474341604
0 199 -0.0009677918131388593
0 200 -0.11441814909230646
0 216 0.035470420808664395
0 225 0.4070214126191669
0 236 0.37905950406277206
0 249 0.08068325233434477
0 255 0.45548019477929547
0 265 0.01077171198427233
0 268 0.14747579610324474
0 273 -0.13205226598507036
0 284 0.6529302190473604
0 285 0.2098017544639595
0 286 -0.24756024669569537
0 289 0.4633559704273789
0 300 0.2500333794129574
0 302 0.008060086507159277
0 304 1.0000000000000002
0 319 0.192219249655

0 23 0.21921641255507318
0 32 0.10002048343437829
0 53 0.27517502746215433
0 63 0.06928481994432427
0 77 -0.10803263271280727
0 107 -0.12139191223511517
0 120 0.41595335107058184
0 165 0.10980367130466533
0 205 0.37929293473524983
0 225 0.4070214126191669
0 236 0.37905950406277206
0 323 -0.040330734115767396
0 328 0.2961077635086205
0 341 -0.10850089590390864
0 342 0.3396291712442968
0 392 -0.059022060724601845
0 404 -0.10690796295599313
0 420 0.44041760541007696
0 430 0.11533618871677369
0 432 0.19547051758087505
0 444 0.5106712325943217
0 477 0.3029967330693013
0 497 -0.20294556351976017
0 498 0.21179383804844476
0 501 -0.6286379546263932
0 522 0.32922757171159106
0 528 0.4110679264365762
0 529 0.15395589755214095
0 530 0.3740631401515296
0 18 0.2741911204736144
0 43 0.11960415567888476
0 46 -0.42046101278394754
0 48 -0.3237676542262997
0 59 0.2984925160650168
0 61 0.3009796665308055
0 84 -0.007196740687944209
0 95 0.037601671376745444
0 108 -0.28847592568777625
0 121 0.1030690170134

0 499 -0.18402137716482936
0 504 0.40750697943372727
0 505 0.20767952187180042
0 506 0.7487767802667673
0 522 0.32922757171159106
0 529 0.15395589755214095
0 530 0.3740631401515296
0 536 -0.07282370620015664
0 538 0.3436657006881627
0 16 0.252503163345075
0 17 0.3256911244376932
0 18 0.2741911204736144
0 26 0.09528133778115049
0 43 0.11960415567888476
0 47 0.29692584078384154
0 58 0.519175597420536
0 59 0.2984925160650168
0 63 0.06928481994432427
0 71 0.5934326313275601
0 82 -0.1192036493541711
0 95 0.037601671376745444
0 110 -0.0015776709255135818
0 115 -0.12539730471813107
0 124 0.10701235768673893
0 129 0.24284553495921973
0 143 -0.04568946553468793
0 160 0.150599415866321
0 165 0.10980367130466533
0 170 0.15568124810739867
0 179 0.45589494817454135
0 199 -0.0009677918131388593
0 201 0.16005580064852515
0 205 0.37929293473524983
0 222 0.1873222557505266
0 225 0.4070214126191669
0 241 0.1759593288625167
0 249 0.08068325233434477
0 255 0.45548019477929547
0 259 0.5462767654822538
0 26

0 261 0.18241049852002025
0 265 0.01077171198427233
0 276 0.154684706636662
0 328 0.2961077635086205
0 365 0.07025723457829394
0 369 0.3114388436629994
0 400 0.28442547248658523
0 408 0.07297563831157718
0 421 -0.11215892098683615
0 428 0.30381786060325583
0 441 -0.16017943545070443
0 448 -0.8064049958557056
0 520 -0.28125181593959153
0 526 0.29809223691515613
0 529 0.15395589755214095
0 538 0.3436657006881627
0 18 0.2741911204736144
0 25 0.22052881541201594
0 43 0.11960415567888476
0 63 0.06928481994432427
0 216 0.035470420808664395
0 261 0.18241049852002025
0 265 0.01077171198427233
0 281 0.7319489475106565
0 282 -0.045659541514770384
0 329 0.7960303845015831
0 335 0.7573111104224233
0 416 0.39076038826545856
0 428 0.30381786060325583
0 499 -0.18402137716482936
0 510 0.07278445357421309
0 25 0.22052881541201594
0 37 -0.11326280437532521
0 40 0.0801193126813568
0 43 0.11960415567888476
0 61 0.3009796665308055
0 63 0.06928481994432427
0 77 -0.10803263271280727
0 84 -0.00719674068794420

...

97 6 -0.25871529050421427
97 7 0.44489245133618016
97 15 0.012235905879720637
97 22 0.3351950462127309
97 30 0.33557309334284124
97 31 -0.04761136571930937
97 33 0
97 36 -1.0
97 37 0.1466116924911839
97 40 0.1281902881859011
97 43 0.021000566183104814
97 50 -0.2165295746681045
97 54 0.917876417567995
97 59 0.05529058834147872
97 61 -0.06172248890715006
97 63 -0.14202916638446386
97 67 0.46817151738642954
97 75 0.029077833977985315
97 79 -0.0185912131366478
97 84 0.16752288594127365
97 95 0.25221534804704876
97 101 -0.04549454907072101
97 114 0.08891833743711997
97 120 0.272904581117903
97 121 0.19354825868966968
97 122 0.47054080061918696
97 128 0.2031818370385526
97 130 -0.19506900858257054
97 139 0.3426233140282872
97 143 0.2148391162596716
97 145 0.3028051246486878
97 147 0.2885792159820177
97 150 0.029943861972775338
97 160 0.13205106561511432
97 165 0.24187325131860682
97 170 0.08203614843744664
97 173 0.5348174745383921
97 176 0.33105576889811056
97 180 0.03922507736895885
97 183

97 466 0.06564936825551611
97 512 0.34916827906635217
97 522 0.17208303842423373
97 540 0.20071928119285903
97 1 -0.0607020648761153
97 9 -0.2075484478525462
97 21 -0.16164860292057984
97 23 -0.051675694759015935
97 26 0.03466959267110248
97 28 0.40748855975678766
97 47 0.07744974821844193
97 48 0.057638292299335675
97 57 0.4102554316672697
97 60 0.6314000362338722
97 63 -0.14202916638446386
97 68 0.1796842594085153
97 71 0.48315265599608986
97 72 -0.3417581858140462
97 81 0.09335866443031694
97 95 0.25221534804704876
97 103 0.2631022042700854
97 104 0.5302376113312398
97 110 0.16951735513119007
97 112 0.08751283168175812
97 115 -0.015108001638348427
97 120 0.272904581117903
97 121 0.19354825868966968
97 127 -0.11505459160558869
97 139 0.3426233140282872
97 160 0.13205106561511432
97 167 0.3004050614985916
97 177 -0.1464673764230117
97 181 0.020893033208217508
97 185 0.41442563832459434
97 190 0.298946321758853
97 191 0.150131466265913
97 192 0.30302223079325646
97 198 0.24749466792903

97 95 0.25221534804704876
97 96 -0.28478312239418613
97 103 0.2631022042700854
97 135 -0.11879051843802109
97 181 0.020893033208217508
97 186 0.2972078358122894
97 198 0.24749466792903915
97 205 0.2705410275504657
97 211 0.15718118630607908
97 216 0.22011267254452552
97 223 0.44869479734039647
97 225 0.18653061833088785
97 261 -0.21408145023174255
97 268 0.3322341843668662
97 270 0.31518266479247764
97 274 0.3717968998522065
97 277 -0.27028411307498185
97 302 0.23399546512705077
97 320 0.20788478917875694
97 340 -0.05382234481966404
97 341 0.10099280728173811
97 342 0.31462126777982613
97 369 0.27914393046994485
97 373 0.563625887649239
97 381 0.08858689449835931
97 425 0.18259798647494216
97 440 -0.5607326876417733
97 461 -0.026693258298732096
97 469 0.17148571600587945
97 493 0.9138690458328996
97 514 0.28657499638012607
97 518 0.03637076799725109
97 522 0.17208303842423373
97 527 0.1817401931153561
97 536 0.09949210364726255
97 540 0.20071928119285903
97 0 0.6672979295912805
97 3 0.

97 144 0.08872032035247135
97 160 0.13205106561511432
97 201 0.019007688872847588
97 225 0.18653061833088785
97 268 0.3322341843668662
97 274 0.3717968998522065
97 285 0.27305120266014515
97 302 0.23399546512705077
97 315 0.32914759389612364
97 336 -0.21203216987838372
97 338 0.13281008541084136
97 368 0.06121804160986785
97 369 0.27914393046994485
97 374 0.4850490860411575
97 400 0.17102132604497872
97 432 0.07016723020272525
97 444 0.05698497803190878
97 466 0.06564936825551611
97 469 0.17148571600587945
97 17 0.24763174825899795
97 26 0.03466959267110248
97 49 -0.23744943375219812
97 63 -0.14202916638446386
97 75 0.029077833977985315
97 112 0.08751283168175812
97 113 -0.15742489957380115
97 160 0.13205106561511432
97 191 0.150131466265913
97 205 0.2705410275504657
97 211 0.15718118630607908
97 212 0.046897382835620005
97 216 0.22011267254452552
97 225 0.18653061833088785
97 249 0.1435911593645466
97 255 0.009508334446775917
97 276 0.14184690270428654
97 296 0.1652241805420338
97 298

KeyboardInterrupt: 

### Evaluation

You should evaluate your predictions using Mean Absolute Error and Root Mean Squared Error. 

In [304]:
# Your Code Here...
# Report Mean Absolute Error and Root Mean Squared Error for test

pearson_MAE, pearson_RMSE = evaluation(pearson_result, test_user_dict, test_counter)    
print(pearson_MAE, pearson_RMSE)  # 0.6903937198616398 0.8991489107420851

0.6917506759527966 0.8983386235087089


### Pearson correlation (varying the threshold)

In [Collaborative Filtering Recommender Systems](http://files.grouplens.org/papers/FnT%20CF%20Recsys%20Survey.pdf), they observe that: 

> Pearson correlation suffers from computing high similarity
between users with few ratings in common. This can be alleviated by setting a threshold on the number of co-rated items
necessary for full agreement (correlation of 1) and scaling the
similarity when the number of co-rated items falls below this
threshold.

So now revise your Pearson to consider a threshold. Try several values and report for one that you think is appropriate.

In [309]:
# Your Code Here...
# Predict for test set
def pearson_threshold(user_dict, id_one, id_two, mean_dict):
    a = 0
    b = 0
    c = 0
    common = 0
    for movie in user_dict.get(id_one):
        if movie in user_dict.get(id_two):
            common += 1
            a += (user_dict.get(id_one).get(movie) - mean_dict.get(id_one)) * (user_dict.get(id_two).get(movie) - mean_dict.get(id_two))
            b += pow(user_dict.get(id_one).get(movie) - mean_dict.get(id_one), 2)
            c += pow(user_dict.get(id_two).get(movie) - mean_dict.get(id_two), 2)
    if b * c == 0:
        return 0;
    elif common > 15:
        return a / math.sqrt(b * c)
    return (common / 15) * a / math.sqrt(b * c)

def pearson_threshold_predict(user, movie, train_user_dict, mean_dict):
    aggregate = 0
    for i in range(len(train_user_dict)):
        if (i is not user) and contains(i, movie, train_user_dict):
            aggregate += (pearson_threshold(train_user_dict, user, i, mean_dict) * (train_user_dict.get(i).get(movie) - mean_dict.get(i)))
    return aggregate * 0.05 


In [310]:
# Your Code Here...
# Report Mean Absolute Error and Root Mean Squared Error for test

threshold_result = {}
for user, movies in test_user_dict.items():
    for movie in movies:
        temp = mean_dict.get(user) + pearson_threshold_predict(user, movie, train_user_dict, mean_dict)
        threshold_result[(user, movie)] = temp

### Evaluation

You should evaluate your predictions using Mean Absolute Error and Root Mean Squared Error. 

In [311]:
threshold_MAE, threshold_RMSE = evaluation(threshold_result, test_user_dict, test_counter)    
print(threshold_MAE, threshold_RMSE)  # 0.6917506759527966 0.8983386235087089

0.685386894114117 0.8905005640168925


What do you observe? How different are your results for the original Pearson Correlation approach vs. the thresholded version vs. the Cosine Similarity approach? Why do you think this is? *provide a brief (1-2 paragraph) discussion based on these questions.*

# Part 2. MF (20 points)

In class, we introduced how matrix factorization works for recommendation. Now it is your term to implement it. There are different methods to obtain the latent factor matrices **P** and **Q**, like gradient descent, Alternating Least Squares (ALS), and so on. Pick one of them and implement your MF model. *You can refer to tutorials and resources online. Remember our **collaboration policy** and you need to inform us of the resources you refer to.* 

Please report MAE and RMSE of your MF model for the test set. *You are expected to get a lower MAE and RMSE compared with the results in Part 1.*

In [ ]:
# Your Code Here...
# Report Mean Absolute Error and Root Mean Squared Error for test



Which method did you use to obtain **P** and **Q**? What are the advantages and disadvantages of the method you pick? *provide a brief (1-2 paragraph) discussion based on these questions.*

# Part 3. Extension (30 points)

Given your results in the previous parts, can you do better? For this last part you should report on your best attempt at improving MAE and RMSE. Provide code, results, plus a brief discussion on your approach. Hints: You may consider using the title or genres information, trying other algorithms, designing a hybrid system, and so on. *As in the last homework, you can do anything you like to improve MAE and RMSE.*

You will get full marks for this part if you get better results than both of your CF and MF (of course we will also judge whether what you do here is reasonable or not). Additionally, you will get 5 points as bonus if your model performs the best among the whole class.

In [ ]:
# Your Code Here...
# Report Mean Absolute Error and Root Mean Squared Error for test



Please explain what you do to improve the recommendation in 1-2 paragraphs.

## Collaboration declarations

*If you collaborated with anyone (see Collaboration policy at the top of this homework), you can put your collaboration declarations here.*

MF: https://datasciencemadesimpler.wordpress.com/tag/alternating-least-squares/
http://www.quuxlabs.com/blog/2010/09/matrix-factorization-a-simple-tutorial-and-implementation-in-python/